# Set up imports

In [30]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [31]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [32]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [33]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [34]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [35]:
data = df.abstract.values.tolist()

In [36]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [37]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [38]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [39]:
# filter words that occur in more than 90% of documents
id2word.filter_extremes(no_above = 0.990)
print(id2word)

Dictionary(4415 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [40]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [41]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [42]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [43]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [44]:
ldaseq.print_topic_times(topic=0)# evolution of 1st topic through all timeslices

[[('image', 0.028874441750290903),
  ('model', 0.024086029119999932),
  ('object', 0.0156444856057198),
  ('feature', 0.012122165133462407),
  ('learning', 0.01157234658779906),
  ('task', 0.008887564147973311),
  ('approach', 0.008131246798448868),
  ('representation', 0.007002164029699829),
  ('method', 0.006764894678000672),
  ('visual', 0.006528247906286946),
  ('training', 0.006361658228796194),
  ('recognition', 0.006285976601784025),
  ('using', 0.006018026675587763),
  ('human', 0.005770687910553854),
  ('network', 0.005738637583584669),
  ('show', 0.005691007837584362),
  ('result', 0.005615822346498394),
  ('word', 0.0052724808785739145),
  ('performance', 0.005265057174596363),
  ('data', 0.005194528586881546)],
 [('image', 0.02875734475068346),
  ('model', 0.024158762496192906),
  ('object', 0.01567326305390889),
  ('feature', 0.01219081230416392),
  ('learning', 0.011593631948379746),
  ('task', 0.008927530339770015),
  ('approach', 0.008165351615494636),
  ('representatio

In [45]:
ldaseq.print_topic_times(topic=1)

[[('model', 0.05405204333129164),
  ('data', 0.018252330020877037),
  ('inference', 0.015002037312446833),
  ('distribution', 0.012715853223425284),
  ('process', 0.01196297425671539),
  ('method', 0.011331671930212594),
  ('variable', 0.009990607337552799),
  ('bayesian', 0.009876834727089216),
  ('latent', 0.009807687695421787),
  ('structure', 0.00920688335374201),
  ('approach', 0.008259226151381725),
  ('probabilistic', 0.007457476503877749),
  ('prior', 0.0072544831205586646),
  ('gaussian', 0.006605246766498038),
  ('using', 0.0061723985893314265),
  ('parameter', 0.005851683358410876),
  ('variational', 0.0055387326207258876),
  ('mixture', 0.005473190291083841),
  ('based', 0.00531729484652802),
  ('topic', 0.00510838753858989)],
 [('model', 0.05408912590347479),
  ('data', 0.01831467166512928),
  ('inference', 0.015048632063269507),
  ('distribution', 0.012751049412292161),
  ('process', 0.011957341671708104),
  ('method', 0.011361799600573968),
  ('variable', 0.0099796470738

In [46]:
ldaseq.print_topic_times(topic=2)

[[('data', 0.02841087694126751),
  ('method', 0.02482085176493826),
  ('feature', 0.017127874134900287),
  ('algorithm', 0.017109666682943076),
  ('learning', 0.012539269860786751),
  ('problem', 0.011349741639430193),
  ('approach', 0.00977297525314991),
  ('task', 0.008105583105011407),
  ('matrix', 0.008060508352280211),
  ('show', 0.007730461538406183),
  ('set', 0.0075536719447467735),
  ('paper', 0.006534553077431838),
  ('proposed', 0.006195608499642583),
  ('using', 0.0060078866833761105),
  ('metric', 0.005750194626580122),
  ('propose', 0.005661780727726598),
  ('ranking', 0.005523096504850848),
  ('analysis', 0.005472420718929001),
  ('similarity', 0.005447232959330166),
  ('distance', 0.005360773408794476)],
 [('data', 0.028495633822711697),
  ('method', 0.02489088830281036),
  ('feature', 0.017169773862998897),
  ('algorithm', 0.017151464366898),
  ('learning', 0.012565172918874164),
  ('problem', 0.011372458526226594),
  ('approach', 0.00979112255539971),
  ('task', 0.008

In [47]:
ldaseq.print_topic_times(topic=3)

[[('distribution', 0.042186227962677965),
  ('gradient', 0.026620607841529607),
  ('estimate', 0.02003189526853395),
  ('test', 0.019242826309366516),
  ('sample', 0.01842256924024366),
  ('training', 0.018124395173307963),
  ('estimator', 0.015247429188363968),
  ('stochastic', 0.01383581604997012),
  ('method', 0.013502025449463273),
  ('data', 0.01102783674603208),
  ('probability', 0.010334243685513927),
  ('domain', 0.009579730867632735),
  ('target', 0.009070099211141455),
  ('show', 0.00851829773739244),
  ('divergence', 0.008276004795172752),
  ('variance', 0.007864939622959161),
  ('sampling', 0.007816656124461177),
  ('descent', 0.007336773085666729),
  ('bias', 0.007029032481200049),
  ('parameter', 0.007002214310887985)],
 [('distribution', 0.04230315563175828),
  ('gradient', 0.026681759550306983),
  ('estimate', 0.02007344101301921),
  ('test', 0.01928083010836471),
  ('sample', 0.01845778151607113),
  ('training', 0.018159413635225573),
  ('estimator', 0.0152739709027397

In [48]:
ldaseq.print_topic_times(topic=4)

[[('algorithm', 0.05185554254656239),
  ('bound', 0.0358933805908766),
  ('learning', 0.020415861994865014),
  ('online', 0.017081956568315914),
  ('regret', 0.011159678241386417),
  ('problem', 0.0104005905962594),
  ('complexity', 0.009959383770548882),
  ('result', 0.00985047212690073),
  ('setting', 0.009229320537945007),
  ('show', 0.009014833653089874),
  ('loss', 0.00848898156042558),
  ('case', 0.008138161148043511),
  ('time', 0.007889748716085778),
  ('function', 0.006883527272373041),
  ('new', 0.00658248142075536),
  ('lower', 0.00657081571031394),
  ('number', 0.006440040878423156),
  ('provide', 0.005776929808681036),
  ('also', 0.005712740956099924),
  ('class', 0.005688564081960286)],
 [('algorithm', 0.05202352108114887),
  ('bound', 0.03599707521183126),
  ('learning', 0.020464533482210005),
  ('online', 0.01711997780001558),
  ('regret', 0.011178770859816566),
  ('problem', 0.01041880047779559),
  ('complexity', 0.009976217072685927),
  ('result', 0.009867216145153115

In [49]:
ldaseq.print_topic_times(topic=5)

[[('problem', 0.020633148817156742),
  ('algorithm', 0.01690594590516146),
  ('method', 0.014561685201747538),
  ('sparse', 0.01240255260928149),
  ('matrix', 0.011803648216714995),
  ('convex', 0.010943900230406213),
  ('function', 0.009812560442520294),
  ('optimization', 0.008809381419536041),
  ('convergence', 0.008518640260340158),
  ('estimation', 0.007961328234337544),
  ('result', 0.007684007016883479),
  ('show', 0.007264156743105349),
  ('linear', 0.007171494276012092),
  ('rate', 0.006947771675220314),
  ('regression', 0.006833434359147766),
  ('analysis', 0.0061755955591545645),
  ('norm', 0.0061453704527628696),
  ('paper', 0.0061057790816380405),
  ('regularization', 0.005647797991545186),
  ('also', 0.005525015665407396)],
 [('problem', 0.02070140621730426),
  ('algorithm', 0.01687117203487577),
  ('method', 0.014602501101027262),
  ('sparse', 0.012433352533904636),
  ('matrix', 0.011833422963594601),
  ('convex', 0.010970571716625537),
  ('function', 0.00983521897697954

In [50]:
ldaseq.print_topic_times(topic=6)

[[('algorithm', 0.025003326897954148),
  ('problem', 0.022237976730793786),
  ('learning', 0.015152105993571035),
  ('function', 0.014016414471866806),
  ('policy', 0.012391380504685488),
  ('method', 0.011415533987660277),
  ('approach', 0.010845758668710265),
  ('show', 0.009260942808681998),
  ('state', 0.00861813630961461),
  ('solution', 0.007214027655833147),
  ('approximation', 0.007088042725015772),
  ('optimization', 0.005711697093207738),
  ('value', 0.005679254278711178),
  ('paper', 0.005613059939415835),
  ('using', 0.005485686245032975),
  ('search', 0.005385667231581794),
  ('optimal', 0.005307480208630699),
  ('reinforcement', 0.005261955176713318),
  ('new', 0.005128858158306438),
  ('approximate', 0.004863127806752906)],
 [('algorithm', 0.02507642355891416),
  ('problem', 0.022300469743412002),
  ('learning', 0.01518827046498065),
  ('function', 0.0140494646987416),
  ('policy', 0.01241930326190439),
  ('method', 0.01144004017894878),
  ('approach', 0.0108686313239275

In [51]:
ldaseq.print_topic_times(topic=7)

[[('clustering', 0.03066672022822686),
  ('information', 0.02890309329880317),
  ('cluster', 0.020271284186869812),
  ('data', 0.017003523571858102),
  ('algorithm', 0.01299070900843711),
  ('query', 0.012914021612170134),
  ('problem', 0.011913673031611723),
  ('user', 0.011582888591107126),
  ('set', 0.010094499179118244),
  ('model', 0.009849921038313603),
  ('item', 0.008360467998922094),
  ('paper', 0.006265127140395797),
  ('distributed', 0.0060800963546860124),
  ('decision', 0.006039656198520929),
  ('may', 0.005999724180359251),
  ('two', 0.005858389778564486),
  ('number', 0.005431869641602902),
  ('one', 0.005323464118580981),
  ('communication', 0.0052977925106775636),
  ('show', 0.005283639504359437)],
 [('clustering', 0.030750847641392725),
  ('information', 0.028980555448831193),
  ('cluster', 0.020319256633950462),
  ('data', 0.017040669410843718),
  ('algorithm', 0.01301559749542335),
  ('query', 0.012938215481472422),
  ('problem', 0.011934988654190402),
  ('user', 0.

In [52]:
ldaseq.print_topic_times(topic=8)

[[('model', 0.016190241246752095),
  ('neural', 0.015432458407960429),
  ('network', 0.013962080438570992),
  ('neuron', 0.012654538865457513),
  ('stimulus', 0.010215747607688936),
  ('activity', 0.009050018175175364),
  ('brain', 0.008226484200984709),
  ('spike', 0.008143775886065446),
  ('response', 0.008051237875890571),
  ('signal', 0.00770137407305445),
  ('show', 0.007264225776877188),
  ('system', 0.007197109875653961),
  ('dynamic', 0.00664972714458793),
  ('input', 0.006362047022838715),
  ('population', 0.005512957765747842),
  ('time', 0.005081119526912755),
  ('pattern', 0.004954369020761039),
  ('information', 0.004921657134044433),
  ('memory', 0.004779585005586416),
  ('state', 0.004707557234144972)],
 [('model', 0.01625072902513258),
  ('neural', 0.015286750100629343),
  ('network', 0.01385451355895555),
  ('neuron', 0.012728253265217725),
  ('stimulus', 0.01026649562841233),
  ('activity', 0.009091105594332119),
  ('brain', 0.00826137285798354),
  ('spike', 0.0081780

In [53]:
ldaseq.print_topic_times(topic=9)

[[('learning', 0.030374177681142984),
  ('kernel', 0.02495182219009903),
  ('graph', 0.014101701891577386),
  ('problem', 0.013450172793332719),
  ('classification', 0.012531813692724632),
  ('method', 0.01076247920782276),
  ('classifier', 0.010680508796361989),
  ('algorithm', 0.01047138476451289),
  ('function', 0.010453578709385134),
  ('data', 0.010226418569290418),
  ('label', 0.009778240318916666),
  ('show', 0.008695893252271),
  ('approach', 0.00761511785780463),
  ('loss', 0.007479142769293231),
  ('class', 0.007142885300346376),
  ('based', 0.0066183355613756234),
  ('prediction', 0.006267119700628692),
  ('space', 0.005992134959052798),
  ('performance', 0.005980233393866643),
  ('framework', 0.005878857486298641)],
 [('learning', 0.030460240299499015),
  ('kernel', 0.025020217513686754),
  ('graph', 0.014131402124907861),
  ('problem', 0.01347814973868051),
  ('classification', 0.012557003442071862),
  ('method', 0.010782521181588524),
  ('classifier', 0.010700503690924726

In [54]:

# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[5.69178290e-02 9.20587101e-01 2.12314225e-04 2.12314225e-04
 2.12314225e-04 2.12314225e-04 2.10088704e-02 2.12314225e-04
 2.12314225e-04 2.12314225e-04]


In [55]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [56]:
ldaseq.print_topic_times(1) # evolution of values for all time slice for topic 2


[[('model', 0.05405204333129164),
  ('data', 0.018252330020877037),
  ('inference', 0.015002037312446833),
  ('distribution', 0.012715853223425284),
  ('process', 0.01196297425671539),
  ('method', 0.011331671930212594),
  ('variable', 0.009990607337552799),
  ('bayesian', 0.009876834727089216),
  ('latent', 0.009807687695421787),
  ('structure', 0.00920688335374201),
  ('approach', 0.008259226151381725),
  ('probabilistic', 0.007457476503877749),
  ('prior', 0.0072544831205586646),
  ('gaussian', 0.006605246766498038),
  ('using', 0.0061723985893314265),
  ('parameter', 0.005851683358410876),
  ('variational', 0.0055387326207258876),
  ('mixture', 0.005473190291083841),
  ('based', 0.00531729484652802),
  ('topic', 0.00510838753858989)],
 [('model', 0.05408912590347479),
  ('data', 0.01831467166512928),
  ('inference', 0.015048632063269507),
  ('distribution', 0.012751049412292161),
  ('process', 0.011957341671708104),
  ('method', 0.011361799600573968),
  ('variable', 0.0099796470738

In [57]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.8730577700978857
CV1 0.38736593570938777
U_Mass2 -1.8724745642912424
CV2 0.38736593570938777
U_Mass3 -1.855855240832175
CV3 0.3859344074094115
U_Mass4 -1.8651071248232625
CV4 0.3894132217002607
U_Mass5 -1.847103970269537
CV5 0.3888170724265681
U_Mass6 -1.8339701445680774
CV6 0.39240303669704973
U_Mass7 -1.892394141332988
CV7 0.391123407954124
U_Mass8 -1.9113518792905075
CV8 0.393202288557868
U_Mass9 -1.8557860134727673
CV9 0.38779731529015615
U_Mass10 -1.8709740819564995
CV10 0.38780826649818395
U_Mass11 -1.8745202119615445
CV11 0.3874219752552396
U_Mass12 -1.891016879308549
CV12 0.388449394984821


In [58]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/